# Ulepszona optymalizacja trasy tramwajowej

Ten notebook zawiera ulepszoną wizualizację i optymalizację tras tramwajowych w Krakowie z:
- Zapewnieniem unikatowości przystanków
- Połączeniem tras przez rzeczywiste drogi
- Minimalizacją kątów zakrętu
- Optymalizacją wielu tras jednocześnie

In [1]:
import sys
import os
sys.path.append(os.path.dirname(os.path.dirname(os.path.abspath('__file__'))))

import geopandas as gpd
from src.optimization.route_optimizer import RouteOptimizer, RouteConstraints
from src.visualization.route_visualizer import RouteVisualizer
from scripts.sourcing_data import TramData, OpenStreetMapData
from shapely.geometry import Point, LineString
import folium
import logging
import numpy as np
import random
import matplotlib.pyplot as plt

logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

INFO:scripts.sourcing_data:Logging initialized.


## Pobieranie danych

In [2]:
def load_data(data_dir: str) -> tuple[gpd.GeoDataFrame, gpd.GeoDataFrame, gpd.GeoDataFrame, gpd.GeoDataFrame]:
    """
    Wczytuje dane z plików GeoJSON
    
    Args:
        data_dir: Katalog z danymi
        
    Returns:
        tuple: DataFrames z budynkami, ulicami, przystankami i liniami
    """
    buildings_path = os.path.join(data_dir, 'buildings.geojson')
    streets_path = os.path.join(data_dir, 'streets.geojson')
    stops_path = os.path.join(data_dir, 'stops.geojson')
    lines_path = os.path.join(data_dir, 'lines.geojson')
    
    logger.info("Wczytywanie danych z plików GeoJSON...")
    buildings_df = gpd.read_file(buildings_path)
    streets_df = gpd.read_file(streets_path)
    stops_df = gpd.read_file(stops_path)
    lines_df = gpd.read_file(lines_path)
    
    logger.info(f"Wczytano {len(buildings_df)} budynków")
    logger.info(f"Wczytano {len(streets_df)} ulic")
    logger.info(f"Wczytano {len(stops_df)} przystanków")
    logger.info(f"Wczytano {len(lines_df)} linii tramwajowych")
    return buildings_df, streets_df, stops_df, lines_df

# Wczytanie danych
data_dir = os.path.join(os.path.dirname(os.path.dirname(os.path.abspath('__file__'))), 'data')
buildings_df, streets_df, stops_df, lines_df = load_data(data_dir)

INFO:__main__:Wczytywanie danych z plików GeoJSON...
INFO:__main__:Wczytano 124332 budynków
INFO:__main__:Wczytano 423521 ulic
INFO:__main__:Wczytano 209 przystanków
INFO:__main__:Wczytano 21 linii tramwajowych


## Wizualizacja istniejących danych

In [ ]:
# Inicjalizacja wizualizatora
visualizer = RouteVisualizer(buildings_df, streets_df)

# Tworzenie podstawowej mapy
m = visualizer.create_base_map()

# Dodawanie istniejących linii
for _, row in lines_df.iterrows():
    coords = [(lat, lon) for lon, lat in row.geometry.coords]
    visualizer.plot_route(coords, m, f"Linia {row['line']}", color='gray')

# Dodawanie przystanków
for _, row in stops_df.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=4,
        color='red',
        fill=True,
        popup=f'Przystanek {row.get("name", "Unknown")}',
        tooltip=f'Przystanek {row.get("name", "Unknown")}'
    ).add_to(m)

m

## Ulepszona optymalizacja wielu tras

In [5]:
# Konfiguracja ograniczeń zgodnie z wymaganiami
constraints = RouteConstraints(
    min_distance_between_stops=200,  # 200m między przystankami
    max_distance_between_stops=1500,  # 1500m między przystankami
    max_angle=60,  # maksymalny kąt zakrętu
    min_route_length=3,  # minimalna liczba przystanków
    max_route_length=20,  # maksymalna liczba przystanków
    min_total_length=1000,  # minimalna długość trasy
    max_total_length=15000,  # maksymalna długość trasy
    min_distance_from_buildings=3,  # minimalna odległość od budynków
    angle_weight=0.1  # waga dla kryterium minimalizacji kątów
)

# Inicjalizacja optymalizatora z ulepszonymi funkcjami
optimizer = RouteOptimizer(
    buildings_df=buildings_df,
    streets_df=streets_df,
    stops_df=stops_df,
    lines_df=lines_df,
    constraints=constraints,
    population_size=50,  # Zmniejszono dla szybszego działania z połączonymi trasami
    generations=30,     # Zmniejszono z powodu większej złożoności
    mutation_rate=0.15,  # Zwiększono dla lepszej eksploracji
    crossover_rate=0.8,
    population_weight=0.6,  # Gęstość zabudowy - najważniejsze kryterium
    distance_weight=0.3,    # Odległość między przystankami
    angle_weight=0.1        # Minimalizacja kątów zakrętu
)

logger.info(f"Wagi kryteriów: gęstość={optimizer.population_weight:.2f}, "
           f"odległość={optimizer.distance_weight:.2f}, kąty={optimizer.angle_weight:.2f}")

INFO:src.optimization.route_optimizer:Tworzenie grafu sieci ulic...
INFO:src.optimization.route_optimizer:Wyszukiwanie najgęściej zaludnionych obszarów...
INFO:src.optimization.route_optimizer:Obliczanie gęstości zabudowy dla 209 przystanków...
INFO:src.optimization.route_optimizer:TOP przystanki według gęstości zabudowy:
INFO:src.optimization.route_optimizer:  1. Gęstość: 1641.1 budynków/km², Budynki: 464, Coords: (50.05029039912, 19.94754957912)
INFO:src.optimization.route_optimizer:  2. Gęstość: 1626.9 budynków/km², Budynki: 460, Coords: (50.05209541356, 19.94194647874)
INFO:src.optimization.route_optimizer:  3. Gęstość: 1626.9 budynków/km², Budynki: 460, Coords: (50.079488410479996, 19.89744751164)
INFO:src.optimization.route_optimizer:  4. Gęstość: 1616.3 budynków/km², Budynki: 457, Coords: (50.02376713138, 19.98070262212)
INFO:src.optimization.route_optimizer:  5. Gęstość: 1595.1 budynków/km², Budynki: 451, Coords: (50.041921998839996, 19.9433303787)
INFO:src.optimization.route_o

## Optymalizacja wielu tras z unikatowością przystanków

In [4]:
# OPTYMALIZACJA WIELU TRAS jednocześnie z zapewnieniem unikatowości
logger.info("Rozpoczęcie optymalizacji wielu tras z unikatowymi przystankami...")

# Resetuj używane przystanki na początek
optimizer.reset_used_stops()

# Optymalizuj 3 trasy jednocześnie
multiple_routes = optimizer.optimize_multiple_routes(num_routes=3)

# Przygotowanie danych do wizualizacji
best_routes = []
scores_history = []
route_details = []

logger.info("\n=== PODSUMOWANIE TRAS ===")
for i, (route, score) in enumerate(multiple_routes):
    logger.info(f"\nTrasa {i+1}:")
    logger.info(f"  - Liczba punktów w pełnej trasie: {len(route)}")
    logger.info(f"  - Ogólny wynik: {score:.3f}")
    
    best_routes.append(route)
    scores_history.append(score)
    
    # Wyodrębnij główne przystanki z trasy
    route_stops = optimizer._extract_stops_from_route(route)
    
    # Oblicz szczegółowe wyniki
    density_score = optimizer.calculate_density_score(route)
    distance_score = optimizer.calculate_distance_score(route)
    angle_score = optimizer.calculate_angle_score(route)
    total_length = optimizer._calculate_total_length(route)
    
    details = {
        'route_number': i + 1,
        'stops_count': len(route_stops),
        'total_points': len(route),
        'total_length_km': total_length / 1000,
        'density_score': density_score,
        'distance_score': distance_score,
        'angle_score': angle_score,
        'overall_score': score
    }
    route_details.append(details)
    
    logger.info(f"  - Liczba głównych przystanków: {details['stops_count']}")
    logger.info(f"  - Całkowita długość: {details['total_length_km']:.2f} km")
    logger.info(f"  - Wynik gęstości zabudowy: {details['density_score']:.3f}")
    logger.info(f"  - Wynik odległości: {details['distance_score']:.3f}")
    logger.info(f"  - Wynik prostoty (kąty): {details['angle_score']:.3f}")

# Znajdź najlepszą trasę
if multiple_routes:
    best_route_info = max(multiple_routes, key=lambda x: x[1])
    best_route_idx = multiple_routes.index(best_route_info)
    logger.info(f"\n🏆 NAJLEPSZA TRASA: Trasa {best_route_idx + 1} z wynikiem {best_route_info[1]:.3f}")
else:
    logger.error("❌ Nie udało się znaleźć żadnej trasy!")

logger.info(f"\n📊 Łącznie używanych przystanków: {len(optimizer.used_stops)}")

INFO:__main__:Rozpoczęcie optymalizacji wielu tras z unikatowymi przystankami...
INFO:src.optimization.route_optimizer:Zresetowano używane przystanki
INFO:src.optimization.route_optimizer:Optymalizacja trasy 1/3
INFO:src.optimization.route_optimizer:Liczba dostępnych przystanków: 209
INFO:src.optimization.route_optimizer:Ograniczenia: min_route_length=3, max_route_length=20
INFO:src.optimization.route_optimizer:Tworzę uproszczoną populację...
INFO:src.optimization.route_optimizer:Utworzono uproszczoną populację o rozmiarze 50


## Wizualizacja wyników

In [ ]:
# Tworzenie szczegółowej mapy wszystkich tras
if best_routes:
    # Mapa ze wszystkimi trasami
    m_all = visualizer.create_base_map()
    colors = ['blue', 'red', 'green', 'purple', 'orange']
    
    for i, route in enumerate(best_routes):
        if route:
            color = colors[i % len(colors)]
            
            # Dodaj trasę do mapy
            visualizer.plot_route(route, m_all, f"Trasa {i+1} (wynik: {scores_history[i]:.2f})", 
                                color=color, weight=6, opacity=0.8)
            
            # Dodaj główne przystanki
            route_stops = optimizer._extract_stops_from_route(route)
            for j, stop in enumerate(route_stops):
                folium.Marker(
                    location=[stop[0], stop[1]],
                    popup=f'Trasa {i+1} - Przystanek {j+1}',
                    tooltip=f'T{i+1}P{j+1}',
                    icon=folium.Icon(color='white', icon_color=color, icon='info-sign')
                ).add_to(m_all)
    
    # Dodaj kontrolkę warstw
    folium.LayerControl().add_to(m_all)
    
    display(m_all)
else:
    logger.error("Brak tras do wizualizacji")

## Analiza szczegółowa najlepszej trasy

In [ ]:
if best_routes and multiple_routes:
    # Znajdź najlepszą trasę
    best_route_info = max(multiple_routes, key=lambda x: x[1])
    best_route_idx = multiple_routes.index(best_route_info)
    best_route = best_route_info[0]
    
    logger.info(f"Analiza szczegółowa najlepszej trasy (Trasa {best_route_idx + 1}):")
    
    # Oblicz granice obszaru
    bounds = (
        min(lon for lat, lon in best_route),
        min(lat for lat, lon in best_route),
        max(lon for lat, lon in best_route),
        max(lat for lat, lon in best_route)
    )
    
    # Generuj mapę gęstości dla tej trasy
    logger.info("Generowanie mapy gęstości...")
    density_map = optimizer.density_calculator.get_density_map(
        grid_size=0.001,
        bounds=bounds
    )
    
    # Utwórz mapę z gęstością zabudowy
    m_best = visualizer.create_base_map()
    
    # Dodaj mapę gęstości
    visualizer.plot_density_map(density_map[0], density_map[1], m_best, opacity=0.6)
    
    # Dodaj najlepszą trasę
    visualizer.plot_route(best_route, m_best, 
                         f"Najlepsza trasa (wynik: {best_route_info[1]:.3f})", 
                         color='blue', weight=8)
    
    # Dodaj przystanki z numeracją
    route_stops = optimizer._extract_stops_from_route(best_route)
    for i, stop in enumerate(route_stops):
        folium.Marker(
            location=[stop[0], stop[1]],
            popup=f'Przystanek {i+1}<br>Lat: {stop[0]:.4f}<br>Lon: {stop[1]:.4f}',
            tooltip=f'P{i+1}',
            icon=folium.Icon(color='red', icon='info-sign')
        ).add_to(m_best)
    
    display(m_best)
    
    # Wyświetl statystyki najlepszej trasy
    best_details = route_details[best_route_idx]
    logger.info(f"\n📈 STATYSTYKI NAJLEPSZEJ TRASY:")
    logger.info(f"Liczba przystanków: {best_details['stops_count']}")
    logger.info(f"Całkowita długość: {best_details['total_length_km']:.2f} km")
    logger.info(f"Średnia odległość między przystankami: {best_details['total_length_km']*1000/(best_details['stops_count']-1):.0f} m")
    logger.info(f"Wynik gęstości zabudowy: {best_details['density_score']:.3f}")
    logger.info(f"Wynik odległości: {best_details['distance_score']:.3f}")
    logger.info(f"Wynik prostoty tras: {best_details['angle_score']:.3f}")
    logger.info(f"WYNIK KOŃCOWY: {best_details['overall_score']:.3f}")

## Porównanie wszystkich tras

In [ ]:
if route_details:
    # Tworzenie wykresu porównawczego
    fig, axes = plt.subplots(2, 2, figsize=(15, 10))
    fig.suptitle('Porównanie tras tramwajowych', fontsize=16)
    
    route_numbers = [d['route_number'] for d in route_details]
    
    # Wykres 1: Wyniki poszczególnych kryteriów
    axes[0, 0].bar(route_numbers, [d['density_score'] for d in route_details], 
                   alpha=0.7, label='Gęstość zabudowy', color='blue')
    axes[0, 0].bar(route_numbers, [d['distance_score'] for d in route_details], 
                   alpha=0.7, label='Odległość', color='green', bottom=[d['density_score'] for d in route_details])
    axes[0, 0].bar(route_numbers, [d['angle_score'] for d in route_details], 
                   alpha=0.7, label='Prostota', color='red', 
                   bottom=[d['density_score'] + d['distance_score'] for d in route_details])
    axes[0, 0].set_title('Składniki wyniku końcowego')
    axes[0, 0].set_xlabel('Numer trasy')
    axes[0, 0].set_ylabel('Wynik')
    axes[0, 0].legend()
    
    # Wykres 2: Wynik końcowy
    bars = axes[0, 1].bar(route_numbers, [d['overall_score'] for d in route_details], 
                         color=['gold' if d['overall_score'] == max([rd['overall_score'] for rd in route_details]) 
                               else 'lightblue' for d in route_details])
    axes[0, 1].set_title('Wynik końcowy')
    axes[0, 1].set_xlabel('Numer trasy')
    axes[0, 1].set_ylabel('Wynik końcowy')
    
    # Dodaj wartości na słupkach
    for bar, detail in zip(bars, route_details):
        height = bar.get_height()
        axes[0, 1].text(bar.get_x() + bar.get_width()/2., height + 0.001,
                        f'{detail["overall_score"]:.3f}',
                        ha='center', va='bottom')
    
    # Wykres 3: Długość tras
    axes[1, 0].bar(route_numbers, [d['total_length_km'] for d in route_details], 
                   color='orange', alpha=0.7)
    axes[1, 0].set_title('Długość tras')
    axes[1, 0].set_xlabel('Numer trasy')
    axes[1, 0].set_ylabel('Długość (km)')
    
    # Wykres 4: Liczba przystanków
    axes[1, 1].bar(route_numbers, [d['stops_count'] for d in route_details], 
                   color='purple', alpha=0.7)
    axes[1, 1].set_title('Liczba przystanków')
    axes[1, 1].set_xlabel('Numer trasy')
    axes[1, 1].set_ylabel('Liczba przystanków')
    
    plt.tight_layout()
    plt.show()
    
    # Tabela podsumowująca
    print("\n📊 TABELA PODSUMOWUJĄCA:")
    print("=" * 80)
    print(f"{'Trasa':<6} {'Przyst.':<8} {'Długość':<10} {'Gęstość':<9} {'Odległość':<10} {'Kąty':<8} {'WYNIK':<8}")
    print("=" * 80)
    
    for d in route_details:
        print(f"{d['route_number']:<6} {d['stops_count']:<8} {d['total_length_km']:<10.2f} "
              f"{d['density_score']:<9.3f} {d['distance_score']:<10.3f} {d['angle_score']:<8.3f} "
              f"{d['overall_score']:<8.3f}")
    
    print("=" * 80)